In [ ]:
%pip install --upgrade pip
%pip install sentence-transformers
%pip install transformers
%pip install datasets
%pip install faiss
%pip install torch
%pip install transformers[torch]
%pip install accelerate

In [1]:
import pandas as pd
from datasets import load_dataset

import torch
from sentence_transformers import SentenceTransformer, models

from sklearn.manifold import MDS
from sklearn.cluster import KMeans

import matplotlib.pyplot as plt
from scipy.spatial.distance import squareform
from scipy.spatial import Voronoi, voronoi_plot_2d
import matplotlib.image as mpimg
from transformers import BertTokenizer, BertForTokenClassification
import torch

from transformers import BertTokenizer, BertForTokenClassification, Trainer, TrainingArguments
from sklearn.model_selection import train_test_split
import torch
import os
from datasets import load_metric
import os

/home/vip/victor.henrique/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2023-11-29 17:57:44.845528: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-11-29 17:57:44.887621: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-11-29 17:57:45.612869: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [8]:
os.environ["CUDA_LAUNCH_BLOCKING"] = "1"

# Carregando o corpus
dataset = load_dataset('mac_morpho')
dataset['train'] = dataset['train'].select(range(200)) # TODO: Remover
dataset['validation'] = dataset['validation'].select(range(200)) # TODO: Remover
dataset['test'] = dataset['test'].select(range(200)) # TODO: Remover

max_token_length = 512

# Carregando o tokenizador
tokenizer = BertTokenizer.from_pretrained('neuralmind/bert-base-portuguese-cased')

def encode_examples(examples):
    # Juntando os tokens em uma única string para cada exemplo
    # texts = examples['tokens']
    texts = [tokens for tokens in examples['tokens']]
    texts = ' '.join(texts)
    encodings = tokenizer(texts, truncation=True, padding=True, max_length=512)

    if len(encodings['input_ids']) < max_token_length:
        encodings['input_ids'] = encodings['input_ids'] + [-100]*(max_token_length-len(encodings['input_ids']))
    
    labels = examples['pos_tags']
    if len(labels) < max_token_length:
        labels = labels + [-100]*(max_token_length-len(labels))

    elif len(labels) > max_token_length:
        labels = labels[:max_token_length]

    encodings['labels'] = labels

    if len(encodings['token_type_ids']) < max_token_length:
        encodings['token_type_ids'] = encodings['token_type_ids'] + [0]*(max_token_length-len(encodings['token_type_ids']))
    
    if len(encodings['attention_mask']) < max_token_length:
        encodings['attention_mask'] = encodings['attention_mask'] + [0]*(max_token_length-len(encodings['attention_mask']))

    # labels = examples['pos_tags']
    # encodings['labels'] = labels

    print(examples)
    print(texts)
    # print(type(texts[0]))
    print(encodings)
    print(encodings['input_ids'])
    print(labels)

    print(len(encodings['input_ids']))
    print(len(encodings['labels']))
    print("\n")
    return encodings

encoded_dataset = dataset.map(encode_examples)


Map: 100%|██████████| 200/200 [00:00<00:00, 1062.54 examples/s]


{'id': '0', 'tokens': ['Jersei', 'atinge', 'média', 'de', 'Cr$', '1,4', 'milhão', 'na', 'venda', 'da', 'Pinhal', 'em', 'São', 'Paulo', '.'], 'pos_tags': [14, 19, 14, 15, 22, 7, 14, 9, 14, 9, 3, 15, 3, 3, 24]}
Jersei atinge média de Cr$ 1,4 milhão na venda da Pinhal em São Paulo .
{'input_ids': [101, 4166, 15335, 11903, 2517, 125, 12064, 109, 205, 117, 678, 6271, 229, 5304, 180, 13820, 5954, 173, 710, 1033, 119, 102, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100

{'id': '0', 'tokens': ['Salto', 'sete'], 'pos_tags': [14, 12]}
Salto sete
{'input_ids': [101, 1920, 183, 1118, 102, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -1

Map: 100%|██████████| 200/200 [00:00<00:00, 911.01 examples/s] 



{'id': '0', 'tokens': ['Ainda', 'em', 'dezembro', 'de', '1990', ',', 'foi', 'editada', 'a', 'famosa', '289', ',', 'que', 'modificava', 'a', 'sistemática', 'da', 'arrecadação', 'do', 'ITR', 'e', 'alterava', 'suas', 'alíquotas', '.'], 'pos_tags': [23, 15, 14, 15, 14, 24, 19, 21, 25, 12, 14, 24, 11, 19, 25, 14, 9, 14, 9, 3, 5, 19, 8, 14, 24]}
Ainda em dezembro de 1990 , foi editada a famosa 289 , que modificava a sistemática da arrecadação do ITR e alterava suas alíquotas .
{'input_ids': [101, 2956, 173, 1512, 125, 5737, 117, 262, 20204, 123, 6334, 2593, 22315, 117, 179, 1261, 1268, 256, 123, 20253, 180, 19713, 171, 290, 22321, 22322, 122, 11518, 2836, 675, 313, 8323, 11538, 22281, 119, 102, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -1

Map: 100%|██████████| 200/200 [00:00<00:00, 644.25 examples/s]

{'id': '163', 'tokens': ['Segundo', 'Bogéa', ',', 'mesmo', 'em', 'países', 'de', 'inflação', 'estável', 'existem', 'punições', 'para', 'induzir', 'o', 'contribuinte', 'a', 'recolher', 'os', 'tributos', '.'], 'pos_tags': [15, 3, 24, 18, 15, 14, 15, 14, 12, 19, 14, 15, 19, 25, 14, 15, 19, 25, 14, 24]}
Segundo Bogéa , mesmo em países de inflação estável existem punições para induzir o contribuinte a recolher os tributos .
{'input_ids': [101, 2195, 22223, 22300, 22278, 117, 653, 173, 1775, 125, 16440, 12055, 3572, 5078, 832, 221, 11754, 307, 146, 17229, 175, 123, 21615, 259, 14399, 22281, 119, 102, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -1

In [9]:
# Sample text
text = "Casa"

# Encode text
output = tokenizer.encode_plus(text)

# Print output
print(output)
print(tokenizer.convert_ids_to_tokens(output['input_ids']))

# Decode input_ids
decoded_text = tokenizer.decode(output['input_ids'])

# Print decoded text
print(decoded_text)

{'input_ids': [101, 3052, 102], 'token_type_ids': [0, 0, 0], 'attention_mask': [1, 1, 1]}
['[CLS]', 'Casa', '[SEP]']
[CLS] Casa [SEP]


In [10]:
# print([len(tokens) for tokens in encoded_dataset['train']['tokens']])
# # print(min(len(encoded_dataset['train']['tokens'])))

# Decodificando as primeiras 5 sequências codificadas
for i in range(5):
    print(f"Sequência {i+1}:")
    size = encoded_dataset['train']['input_ids'][i]
    size2 = encoded_dataset['train']['labels'][i]
    print(size)
    print(size2)
    print("\n")


Sequência 1:
[101, 4166, 15335, 11903, 2517, 125, 12064, 109, 205, 117, 678, 6271, 229, 5304, 180, 13820, 5954, 173, 710, 1033, 119, 102, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100

In [11]:
print(encoded_dataset['train']['input_ids'][0])
print(encoded_dataset['train']['labels'][0])
print(len(dataset['train'].features['pos_tags'].feature.names))
# Definindo o modelo
class POSModel(BertForTokenClassification):
    def forward(self, input_ids, attention_mask, labels):
        outputs = super().forward(input_ids, attention_mask, labels)
        loss = outputs.loss
        logits = outputs.logits
        predictions = torch.argmax(logits, dim=-1)
        return loss, predictions

model = POSModel.from_pretrained('neuralmind/bert-base-portuguese-cased', num_labels=len(dataset['train'].features['pos_tags'].feature.names))
# model = model.to('cpu')
# Definindo os argumentos de treinamento
args = TrainingArguments(
    "test-pos",
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=64,
    num_train_epochs=3,
    weight_decay=0.01,
)

# Definindo o treinador
trainer = Trainer(
    model,
    args,
    train_dataset=encoded_dataset['train'],
    eval_dataset=encoded_dataset['validation'],
    tokenizer=tokenizer,
)

# Treinando o modelo

print("Fine-tunning...")
trainer.train()

[101, 4166, 15335, 11903, 2517, 125, 12064, 109, 205, 117, 678, 6271, 229, 5304, 180, 13820, 5954, 173, 710, 1033, 119, 102, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100,

Some weights of POSModel were not initialized from the model checkpoint at neuralmind/bert-base-portuguese-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
  0%|          | 0/39 [04:20<?, ?it/s]


Fine-tunning...


  0%|          | 0/39 [00:00<?, ?it/s]../aten/src/ATen/native/cuda/Indexing.cu:1292: indexSelectLargeIndex: block: [61,0,0], thread: [96,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1292: indexSelectLargeIndex: block: [61,0,0], thread: [97,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1292: indexSelectLargeIndex: block: [61,0,0], thread: [98,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1292: indexSelectLargeIndex: block: [61,0,0], thread: [99,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1292: indexSelectLargeIndex: block: [61,0,0], thread: [100,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1292: indexSelectLargeIndex: block: [61,0,0], thread: [101,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1292: i

RuntimeError: CUDA error: device-side assert triggered
Compile with `TORCH_USE_CUDA_DSA` to enable device-side assertions.
